[View in Colaboratory](https://colab.research.google.com/github/jeffreyrnorton/Notebooks_MachineLearning/blob/master/CNNsWithTensorFlowAndKeras.ipynb)

# TensorFlow vs Keras

I have been very curious about comparing these two packages.  Last summer on a project, our intern selected Keras over everything else because she said it was much easier to use.  She is not the only one who thinks that...

Keras is the [first](http://www.fast.ai/2017/01/03/keras/) *higher-level interface* to be directly integrated into TensorFlow.  I love this comment: **Using TensorFlow makes me feel like I’m not smart enough to use TensorFlow; whereas using Keras makes me feel like neural networks are easier than I realized.**

Let's get started by building a CNN (Convolutional Neural Network) using both TensorFlow and Keras for recognizing handwriting images from the MNIST library of symbols - the classic example.

Per my usual curiosity, I start asking questions like "what is a CNN?"  This is an involved topic, so I am going to give some references to go through and leave it to the reader to give due diligence.

Christopher Olah.  Understanding Convolutions.  http://colah.github.io/posts/2014-07-Understanding-Convolutions/  
Christopher Olah.  Conv Nets: A Modular Perspective.  http://colah.github.io/posts/2014-07-Conv-Nets-Modular/  
DeepLearning.ai. Convolutional Neural Nets (LeNet). http://deeplearning.net/tutorial/lenet.html  
[CS231n: Convolutional Neural Networks for Visual Recognition](http://cs231n.stanford.edu/) Notes, see especially Module 2.  http://cs231n.github.io/  
*Deep Learning Book*, Chapter 9, Convolutional Networks.  http://www.deeplearningbook.org/contents/convnets.html  


# TensorFlow

For TensorFlow, I follow the [tutorial](https://www.tensorflow.org/tutorials/layers) on layers provided by TensorFlow.

### CNN architecture

* [Convolutional Layer](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) \#1: Applies 32 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
* [Pooling Layer](https://www.tensorflow.org/versions/r1.2/api_docs/python/tf/layers/max_pooling2d) \#1: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
* [Convolutional Layer](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) \#2: Applies 64 5x5 filters, with ReLU activation function
* [Pooling Layer](https://www.tensorflow.org/versions/r1.2/api_docs/python/tf/layers/max_pooling2d) \#2: Again, performs max pooling with a 2x2 filter and stride of 2
* [Dense Layer](https://www.tensorflow.org/versions/master/api_docs/python/tf/layers/dense) \#1: 1,024 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
* [Dense Layer](https://www.tensorflow.org/versions/master/api_docs/python/tf/layers/dense) \#2 (Logits Layer): 10 neurons, one for each digit target class (0–9).

and a [dropout](https://www.tensorflow.org/api_docs/python/tf/layers/dropout) layer.

## Platform Notes

The original notebook was developed on Microsoft Free Azure notebooks.  However as we note, these notebooks do not offer GPU computing.  But Google Colaboratory does.  Part of our purpose here is not only to look at TensorFlow vs Keras, but also consider the power of GPU computing in these algorithms.

In [0]:
# Imports
import numpy as np
import tensorflow as tf
import time

tf.logging.set_verbosity(tf.logging.INFO)

def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # -1 - batch size for a 28x28 image with 1 color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1.
    # 32 5x5 filters
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    # 64 5x5 filters
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    
    # Pooling layer #2
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    # 1,024 neurons, with dropout regularization rate of 0.4
    # probability of 0.4 that any given element will be dropped during training)
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    # 10 neurons, one for each digit target class (0–9)
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

### Import Dataset

Import the mnist database.  Originally, we used the line:

```mnist = tf.contrib.learn.datasets.load_dataset("mnist")```

However, when running this on Colaboratory, we get a lot of warnings from using this source.  Apparently, the above is not the *official* version.  The path below is.

In [2]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=False)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.


### Training Data

In [3]:
train_data = mnist.train.images # Returns np.array
print(train_data.shape)

(55000, 784)


In [4]:
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
print(type(train_labels))
print(train_labels.shape)

<class 'numpy.ndarray'>
(55000,)


### Testing Data

In [5]:
test_data = mnist.test.images # Returns np.array
test_labels = np.asarray(mnist.test.labels, dtype=np.int32)
print(test_data.shape)

(10000, 784)


On Dimensions:
* 784 is the number of bytes in a 28x28x1 image
* Of the images, nearly 85% are for training and the remaining are for testing.

### Create the Estimator
The Estimator is a TensorFlow class for performing high-level model training, evaluation, and inference for the model.

In [6]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fa4dfb58a20>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


### Set Up a Logging Hook

Since CNNs can take a while to train, let's set up some logging so we can track progress during training. We can use TensorFlow's tf.train.SessionRunHook to create a tf.train.LoggingTensorHook that will log the probability values from the softmax layer of our CNN.

In [0]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50)

## Train the Model
On this free-tier notebook server, this is terribly slow taking up to one hour of CPU according to the documentation.  It is better to run this on compute with GPU. <a href="#after_compute">Go to after compute.</a>

In [8]:
# Train the model
start=time.time()

train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

print("Training (TensorFlow) Elaspsed Time: {}".format(time.time()-start))


INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from tmp/mnist_convnet_model/model.ckpt-20001
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 20002 into tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.00005128 0.00000216 0.00412246 0.00097617 0.00004842 0.00034478
  0.00010658 0.00000179 0.9943106  0.00003568]
 [0.97797054 0.00005439 0.00005095 0.00022493 0.00026942 0.00007029
  0.00747416 0.00004632 0.00977219 0.00406685]
 [0.00000021 0.00000251 0.99986696 0.00006159 0.         0.00000002
  0.         0.00000001 0.00006867 0.        ]
 [0.00000145 0.00000856 0.00075531 0.00019261 0.00183878 0.00000147
  0.00000025 0.00290913 0.00059994 0.9936925 ]
 [0.00004894 0.00000034 0.00003434 0.0000065  0.0065382  0.00001504
  0.00000048 0.07021663 0.00006889

INFO:tensorflow:probabilities = [[0.00005815 0.6891622  0.01313244 0.00114535 0.01640895 0.0217984
  0.24766718 0.00008354 0.00950476 0.00103904]
 [0.99998355 0.         0.00000963 0.00000095 0.         0.00000215
  0.00000284 0.00000002 0.00000081 0.00000001]
 [0.02247647 0.00005189 0.01558044 0.00044722 0.8497466  0.00237087
  0.09628772 0.00005117 0.01200704 0.00098064]
 [0.00007534 0.9956665  0.00028089 0.00147475 0.00005019 0.00031709
  0.00054678 0.00009241 0.00137673 0.00011933]
 [0.00001235 0.9893861  0.0002554  0.00063888 0.00003476 0.00013492
  0.00020618 0.00010104 0.00912871 0.00010174]
 [0.07471254 0.00000178 0.9162396  0.00273817 0.00070854 0.00184794
  0.00113462 0.00000576 0.00220416 0.00040697]
 [0.00085062 0.00000763 0.00016416 0.00001866 0.00013237 0.00374861
  0.99220955 0.00000002 0.00286186 0.00000645]
 [0.00000573 0.00953072 0.9888932  0.0003771  0.00000139 0.00001083
  0.00003368 0.0001071  0.00102857 0.00001169]
 [0.00000524 0.01855754 0.000108   0.00401452 0.3

INFO:tensorflow:probabilities = [[0.00005203 0.00000012 0.00005573 0.00004295 0.00463122 0.00855112
  0.9860888  0.00000009 0.0003977  0.00018014]
 [0.00000004 0.00000044 0.00000091 0.00023713 0.00060695 0.00001877
  0.         0.00054072 0.00025552 0.99833953]
 [0.00000286 0.00000002 0.00000013 0.00005656 0.00000042 0.999928
  0.00000043 0.00000035 0.00000046 0.0000106 ]
 [0.         0.         0.00000001 0.00000002 0.9998603  0.0000001
  0.00000001 0.00000563 0.00000188 0.00013214]
 [0.00125958 0.00000012 0.00403937 0.00000085 0.15810163 0.00003954
  0.8323699  0.00169713 0.00101407 0.00147776]
 [0.00001912 0.9822765  0.00104288 0.00569594 0.00002147 0.00028803
  0.00000377 0.00182906 0.00777156 0.00105177]
 [0.9997485  0.00000001 0.00021486 0.00000067 0.00000091 0.00000048
  0.00003083 0.00000008 0.00000102 0.00000272]
 [0.00000064 0.00002389 0.00004796 0.99923384 0.00000174 0.00023792
  0.00000145 0.00010694 0.00027566 0.0000699 ]
 [0.9997583  0.         0.00007419 0.00000041 0.000

INFO:tensorflow:probabilities = [[0.00004069 0.00027101 0.00109284 0.08330389 0.02965164 0.00336517
  0.00057781 0.00040958 0.80317533 0.078112  ]
 [0.00000685 0.98852867 0.00010131 0.00074855 0.0000653  0.0000506
  0.00002453 0.00759921 0.00227273 0.00060228]
 [0.         0.00000025 0.00002091 0.9996618  0.00000002 0.00006321
  0.         0.         0.00025292 0.00000092]
 [0.0005468  0.00349082 0.93843555 0.01735284 0.00151955 0.00052305
  0.00076449 0.00227068 0.03351101 0.0015851 ]
 [0.00000318 0.00000003 0.0000345  0.0000278  0.00000012 0.00005727
  0.00000281 0.00000008 0.9998698  0.0000044 ]
 [0.00001101 0.00000086 0.00000042 0.00001249 0.00000068 0.9999317
  0.00001712 0.00000272 0.0000214  0.00000156]
 [0.00009871 0.00000862 0.00016313 0.00128487 0.01122683 0.00006916
  0.00001014 0.02511384 0.00084463 0.9611801 ]
 [0.02231504 0.00000041 0.00022035 0.00022463 0.00407815 0.00267567
  0.00000205 0.94015783 0.00072244 0.02960357]
 [0.00000023 0.00000012 0.00000001 0.00000359 0.00

INFO:tensorflow:probabilities = [[0.9999279  0.         0.00002231 0.00002511 0.         0.00002031
  0.00000003 0.00000155 0.00000092 0.00000178]
 [0.00000303 0.00008783 0.99869233 0.00102997 0.00000316 0.00000041
  0.00002777 0.00013759 0.00001778 0.00000018]
 [0.01180225 0.00003313 0.80903274 0.12939966 0.00077891 0.01617058
  0.00216322 0.00420063 0.02288282 0.00353608]
 [0.00087342 0.00020082 0.00012287 0.05975779 0.02376155 0.8476729
  0.01354198 0.00109789 0.00527555 0.0476953 ]
 [0.00000246 0.00011946 0.20060126 0.01540355 0.05187725 0.00011598
  0.00027002 0.727209   0.00089666 0.00350433]
 [0.00000893 0.99720323 0.00016192 0.00053564 0.00012749 0.00000872
  0.00001318 0.00129173 0.00056124 0.00008796]
 [0.00029228 0.00000193 0.00225805 0.02369411 0.00000424 0.00044702
  0.00000118 0.00014599 0.9721416  0.00101359]
 [0.00000036 0.00012701 0.00021668 0.9995664  0.         0.00006894
  0.         0.00000005 0.00002056 0.00000004]
 [0.00000212 0.00000433 0.00001631 0.00008385 0.0

...

INFO:tensorflow:probabilities = [[0.         0.00139231 0.99860495 0.00000175 0.         0.
  0.00000004 0.00000009 0.00000086 0.        ]
 [0.9999162  0.         0.00002899 0.00000001 0.00000001 0.00000025
  0.00005444 0.00000001 0.         0.0000001 ]
 [0.         0.         0.00000075 0.99975103 0.         0.00001685
  0.         0.00000004 0.00014794 0.00008341]
 [0.         0.00025155 0.9995832  0.00002109 0.         0.00000005
  0.00000001 0.00000509 0.000139   0.        ]
 [0.00000028 0.00000352 0.00015066 0.99748355 0.00000049 0.00103024
  0.         0.00000003 0.0006067  0.00072459]
 [0.00000122 0.99950373 0.00000621 0.00000297 0.00003067 0.00000235
  0.00002536 0.00000101 0.00042618 0.00000034]
 [0.00000208 0.00000017 0.00001072 0.00004121 0.00116559 0.00000072
  0.00000005 0.00060996 0.00004545 0.99812406]
 [0.         0.00000022 0.999997   0.00000214 0.00000006 0.00000001
  0.         0.00000043 0.00000014 0.        ]
 [0.00206846 0.00000079 0.03717163 0.00001792 0.00013925

INFO:tensorflow:probabilities = [[0.0000119  0.00000023 0.00060362 0.00464075 0.00008531 0.00000264
  0.00000065 0.9168011  0.00018315 0.07767066]
 [0.00055161 0.00011432 0.02518377 0.00002758 0.00469522 0.00353774
  0.96543515 0.00000286 0.00037406 0.00007766]
 [0.         0.00000002 0.00000175 0.99823797 0.00000002 0.00003405
  0.         0.00001427 0.00168805 0.00002389]
 [0.00935992 0.00021394 0.00022657 0.00302398 0.00062035 0.35350758
  0.07371534 0.00007599 0.54882807 0.01042824]
 [0.00001215 0.9989292  0.00006822 0.00003337 0.00026517 0.00002783
  0.00015158 0.00029544 0.00012144 0.0000956 ]
 [0.00016133 0.00000004 0.00000444 0.00000018 0.00001235 0.00112928
  0.9986897  0.         0.0000026  0.00000008]
 [0.00004686 0.00000169 0.00008742 0.00000346 0.99971956 0.00000338
  0.0000028  0.00000461 0.00000212 0.00012819]
 [0.00000043 0.0000101  0.9999337  0.00001335 0.00000805 0.00002708
  0.00000622 0.00000028 0.00000086 0.00000001]
 [0.         0.         0.         0.00010213 0.

INFO:tensorflow:probabilities = [[0.99937373 0.00000387 0.00021747 0.00001646 0.         0.00021443
  0.00000205 0.00008654 0.00000013 0.00008525]
 [0.00000009 0.00000001 0.00000385 0.00000042 0.00000013 0.00000248
  0.00000037 0.00000014 0.9999912  0.00000127]
 [0.00000052 0.00000005 0.00000178 0.00000018 0.0000032  0.00000003
  0.         0.99995184 0.00000135 0.0000411 ]
 [0.00000065 0.00000036 0.00590768 0.00072886 0.00000001 0.00000001
  0.         0.993152   0.00004654 0.00016384]
 [0.         0.         0.         0.9998173  0.         0.00000262
  0.         0.00000005 0.00000219 0.00017785]
 [0.0000027  0.99973947 0.00005232 0.00008841 0.00000482 0.00000521
  0.00001139 0.00001383 0.00007738 0.00000435]
 [0.00000307 0.00000031 0.00001459 0.00053741 0.00007697 0.00003998
  0.00000005 0.00104829 0.00045002 0.9978294 ]
 [0.         0.         0.00000003 0.00021557 0.         0.99977916
  0.00000027 0.         0.00000502 0.00000003]
 [0.9999269  0.         0.00000748 0.00000056 0.

INFO:tensorflow:probabilities = [[0.00042526 0.00000137 0.00003075 0.00001149 0.00018968 0.00018012
  0.9991485  0.00000036 0.00001144 0.00000112]
 [0.00000154 0.998885   0.000038   0.00009848 0.00027602 0.00012554
  0.00007691 0.00006538 0.00042211 0.00001112]
 [0.00000183 0.00000002 0.00001782 0.00000003 0.9996995  0.0000004
  0.00027532 0.00000242 0.00000239 0.00000035]
 [0.00004676 0.00000076 0.00008846 0.00070638 0.00002268 0.00047434
  0.00000151 0.00015737 0.9928716  0.00563017]
 [0.00027671 0.61893183 0.00038386 0.00357996 0.0000452  0.0001282
  0.00000856 0.36723202 0.00719914 0.00221455]
 [0.00000037 0.000001   0.0009441  0.00000049 0.9984004  0.00000522
  0.00063361 0.00000768 0.00000057 0.00000654]
 [0.00000001 0.00000193 0.99760616 0.00019102 0.00000015 0.00000002
  0.00000016 0.00219676 0.00000375 0.        ]
 [0.99991155 0.00000019 0.00001231 0.00000071 0.00000019 0.00002169
  0.0000063  0.00002085 0.0000012  0.00002506]
 [0.00000001 0.00000032 0.00008619 0.9998487  0.  

Training (TensorFlow) Elaspsed Time: 235.59738945960999


<p id="after_compute">Note it took 10845 seconds or over 3 hours to train without GPU using the Microsoft Azure notebook.  On Google Colaboratory with a GPU processor, training took 235 seconds - less than **4 minutes**.  That is why these problems have to be run with GPU.</p>

## Evaluate the Model

In [9]:
# Evaluate the model and print results
start=time.time()

eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": test_data},
    y=test_labels,
    num_epochs=1,
    shuffle=False)
test_results = mnist_classifier.evaluate(input_fn=eval_input_fn)

print("Testing (TensorFlow) Elaspsed Time: {}".format(time.time()-start))

print(test_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-05-09-05:45:59
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from tmp/mnist_convnet_model/model.ckpt-40001
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-05-09-05:46:00
INFO:tensorflow:Saving dict for global step 40001: accuracy = 0.9802, global_step = 40001, loss = 0.06150935
Testing (TensorFlow) Elaspsed Time: 0.9405736923217773
{'accuracy': 0.9802, 'loss': 0.06150935, 'global_step': 40001}


# Keras

Consider building a [CNN with Keras](https://elitedatascience.com/keras-tutorial-deep-learning-in-python). The network is modified to match the TensorFlow network given above and updated to the current version of Keras as of March 2018.

The first thing is that Keras works with multiple backends.  By default, it uses TensorFlow.  We are going to swap to Theano so we are going to very explicit on our backends.

In [10]:
from keras import backend as K
import os, importlib

def set_keras_backend(backend):

    if K.backend() != backend:
        os.environ['KERAS_BACKEND'] = backend
        importlib.reload(K)
        assert K.backend() == backend

Using TensorFlow backend.


In [0]:
set_keras_backend("tensorflow")

In [12]:
print(K.backend())

tensorflow


In [0]:
# 1. Import libraries and modules
import time

import numpy as np
np.random.seed(123)  # for reproducibility
 
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Convolution2D, MaxPooling2D
from keras.utils import np_utils
from keras.datasets import mnist
 
# 2. Load pre-shuffled MNIST data into train and test sets
(X_train, y_train), (X_test, y_test) = mnist.load_data()
 
# 3. Preprocess input data
X_train = X_train.reshape(X_train.shape[0], 28, 28, 1)
X_test = X_test.reshape(X_test.shape[0], 28, 28, 1)
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
X_train /= 255
X_test /= 255
 
# 4. Preprocess class labels
Y_train = np_utils.to_categorical(y_train, 10)
Y_test = np_utils.to_categorical(y_test, 10)

### CNN architecture

* [Convolutional Layer](https://faroit.github.io/keras-docs/1.2.2/layers/convolutional/#convolution2d) \#1: Applies 32 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
* [Pooling Layer](https://keras.io/layers/pooling/#maxpooling2d) \#1: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
* [Convolutional Layer](https://faroit.github.io/keras-docs/1.2.2/layers/convolutional/#convolution2d) \#2: Applies 64 5x5 filters, with ReLU activation function
* [Pooling Layer](https://keras.io/layers/pooling/#maxpooling2d) \#2: Again, performs max pooling with a 2x2 filter and stride of 2
* [Dense Layer](https://keras.io/layers/core/#dense) \#1: 1,024 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
* [Dense Layer](https://keras.io/layers/core/#dense) \#2 (Logits Layer): 10 neurons, one for each digit target class (0–9).

and the [Dropout](https://keras.io/layers/core/#dropout) layer.

In [0]:
# 5. Define model architecture
model = Sequential()

model.add(Convolution2D(32, (5, 5), activation='relu', input_shape=(28,28,1)))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Convolution2D(64, (5, 5), activation='relu'))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Flatten())
model.add(Dense(1024, activation='relu'))
model.add(Dropout(0.4))
model.add(Dense(10, activation='softmax'))

In [0]:
# 6. Compile model
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
 

In [16]:
# 7. Fit model on training data
start=time.time()

model.fit(X_train, Y_train, 
          batch_size=32, epochs=10, verbose=1)

print("Training (Keras) Elaspsed Time: {}".format(time.time()-start))

Epoch 1/10
60000/60000 [==============================] - 23s 378us/step - loss: 0.1166 - acc: 0.9637
Epoch 2/10
48544/60000 [=======================>......] - ETA: 4s - loss: 0.0408 - acc: 0.9873

60000/60000 [==============================] - 22s 369us/step - loss: 0.0410 - acc: 0.9873
Epoch 3/10
60000/60000 [==============================] - 22s 367us/step - loss: 0.0285 - acc: 0.9911
Epoch 4/10
10784/60000 [====>.........................] - ETA: 18s - loss: 0.0178 - acc: 0.9943

60000/60000 [==============================] - 22s 368us/step - loss: 0.0233 - acc: 0.9925
Epoch 5/10
60000/60000 [==============================] - 22s 367us/step - loss: 0.0190 - acc: 0.9939
Epoch 6/10


60000/60000 [==============================] - 22s 370us/step - loss: 0.0158 - acc: 0.9949
Epoch 7/10
54720/60000 [==========================>...] - ETA: 1s - loss: 0.0103 - acc: 0.9969

60000/60000 [==============================] - 22s 369us/step - loss: 0.0115 - acc: 0.9966
Epoch 8/10
60000/60000 [==============================] - 22s 373us/step - loss: 0.0119 - acc: 0.9966
Epoch 9/10
12256/60000 [=====>........................] - ETA: 17s - loss: 0.0108 - acc: 0.9966

60000/60000 [==============================] - 22s 368us/step - loss: 0.0115 - acc: 0.9965
Epoch 10/10
60000/60000 [==============================] - 22s 372us/step - loss: 0.0105 - acc: 0.9969
Training (Keras) Elaspsed Time: 222.56406688690186


Training with Keras on Microsoft Azure (*no GPU*) takes 1753 seconds or about 29 minutes to train.  On Google Colaboratory with a GPU, training took 223 seconds (less than 6 minutes).  That is about the same time as TensorFlow.  This makes far more sense to me - I'm wondering if the Azure notebook framework has a bug in the platform?

In any case, we really need GPUs for training!

In [17]:
# 8. Evaluate model on test data
start=time.time()

score = model.evaluate(X_test, Y_test, verbose=0)

print("Testing (Keras) Elaspsed Time: {}".format(time.time()-start))

print("Loss={}, Accuracy={}".format(score[0], score[1]))

Testing (Keras) Elaspsed Time: 1.1371347904205322
Loss=0.03921633380714825, Accuracy=0.9915


### Visualizing Keras Models

We found this later, but following is how to visualize the network.  This is the CNN we are using.  The [Keras Documentation](https://keras.io/visualization/) shows how to display the models.  It works on Azure, but it does not work on Colaboratory.

(On Colaboratory, it asks to install pydot - even with the install, the model_to_dot still does not work!)

# Prelude to Summary

Admittedly, Keras does present a better (less complicated) interface then TensorFlow, but I really struggled a bit around building up the layers.  It seemed to me that the shorthand was a bit too terse and I had to work a bit to get through a few issues with the Convolution2D layer.

There are a couple of other things to really like about Keras.  Whereas in TensorFlow we had to jump through hoops to see what was going on, Keras presented a simple way to print out progress.

On Azure,  I noticed is that Keras is amazingly fast - but how can that be since TensorFlow is the backend?  It might be a question of how the two packages handle the computing environment (multi-threading, GPU usage).
We can run a few studies and tests to determine if this is the case.  First, the TensorFlow documentation for the [convolution](https://www.tensorflow.org/api_docs/python/tf/nn/conv2d) has a flag for running CUDA on GPUs.

We note that on Google Colaboratory, the run times make a lot more sense and with a GPU processor, the performance improves by many orders of magnitude.

In [18]:
import multiprocessing
import tensorflow as tf

print('Number of CPU Cores: {}'.format(multiprocessing.cpu_count()))

print('GPU available for TensorFlow : {}'.format(tf.test.is_gpu_available()))

Number of CPU Cores: 2
GPU available for TensorFlow : True


With the Azure notebook, we had two CPU cores and no GPU.  On Colaboratory, we also had two CPU cores, but also a GPU core.  TensorFlow is optimized to run with GPUs.  I would love to be able to run this on Colaboratory with a TPU (Tensor Processing Unit) - see [this article](https://cloud.google.com/blog/big-data/2017/05/an-in-depth-look-at-googles-first-tensor-processing-unit-tpu) on TPUs).

With Azure, Keras runs the training in under one hour with three times the steps as TensorFlow. With the extra training, Keras is delivering better accuracy with less loss, but there could be another factor.

I thought perhaps I had made a mistake, but running with Colaboratory indicates that the problem is probably on the Azure platform.  Training on Colaboratory with TensorFlow and Keras in roughly the same time frame which is what we expected.

**What about Theano?**  The [DeepLearning.ai reference](http://deeplearning.net/tutorial/lenet.html) uses [Theano](http://deeplearning.net/software/theano/).  Theano is another low-level compute engine like TensorFlow.  There are [many opinions](https://www.reddit.com/r/MachineLearning/comments/4ekywt/tensorflow_vs_theano_which_to_learn/) on which to learn.  That is why Keras is so powerful - Keras also [wraps](https://keras.io/backend/) on top of Theano!  So let's show how to swap backends and run with Theano!

In [0]:
from keras import backend as K
import os, importlib

def set_keras_backend(backend):

    if K.backend() != backend:
        os.environ['KERAS_BACKEND'] = backend
        importlib.reload(K)
        assert K.backend() == backend

In [0]:
set_keras_backend("theano")

In [23]:
print(K.backend())

theano


In [0]:
# 1. Import libraries and modules
import time

import numpy as np
np.random.seed(123)  # for reproducibility
 
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten
from keras.layers import Convolution2D, MaxPooling2D
from keras.utils import np_utils
from keras.datasets import mnist
 
# 2. Load pre-shuffled MNIST data into train and test sets
(X_train, y_train), (X_test, y_test) = mnist.load_data()
 
# 3. Preprocess input data
X_train = X_train.reshape(X_train.shape[0], 28, 28, 1)
X_test = X_test.reshape(X_test.shape[0], 28, 28, 1)
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
X_train /= 255
X_test /= 255
 
# 4. Preprocess class labels
Y_train = np_utils.to_categorical(y_train, 10)
Y_test = np_utils.to_categorical(y_test, 10)

In [0]:
# 5. Define model architecture
model = Sequential()

model.add(Convolution2D(32, (5, 5), activation='relu', input_shape=(28,28,1)))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Convolution2D(64, (5, 5), activation='relu'))
model.add(MaxPooling2D(pool_size=(2,2), strides=2))
model.add(Flatten())
model.add(Dense(1024, activation='relu'))
model.add(Dropout(0.4))
model.add(Dense(10, activation='softmax'))

In [0]:
# 6. Compile model
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
 

In [27]:
# 7. Fit model on training data
start=time.time()

model.fit(X_train, Y_train, 
          batch_size=32, epochs=10, verbose=1)

print("Training (Keras) Elaspsed Time: {}".format(time.time()-start))

Epoch 1/10
60000/60000 [==============================] - 23s 376us/step - loss: 0.1169 - acc: 0.9636
Epoch 2/10
48160/60000 [=======================>......] - ETA: 4s - loss: 0.0401 - acc: 0.9874

60000/60000 [==============================] - 22s 373us/step - loss: 0.0409 - acc: 0.9871
Epoch 3/10
60000/60000 [==============================] - 22s 372us/step - loss: 0.0291 - acc: 0.9912
Epoch 4/10
10528/60000 [====>.........................] - ETA: 18s - loss: 0.0187 - acc: 0.9934

60000/60000 [==============================] - 22s 374us/step - loss: 0.0217 - acc: 0.9929
Epoch 5/10
58976/60000 [============================>.] - ETA: 0s - loss: 0.0188 - acc: 0.9944

60000/60000 [==============================] - 22s 372us/step - loss: 0.0191 - acc: 0.9943
Epoch 6/10
60000/60000 [==============================] - 22s 372us/step - loss: 0.0157 - acc: 0.9953
Epoch 7/10
13568/60000 [=====>........................] - ETA: 17s - loss: 0.0114 - acc: 0.9963

60000/60000 [==============================] - 22s 371us/step - loss: 0.0151 - acc: 0.9954
Epoch 8/10
60000/60000 [==============================] - 22s 369us/step - loss: 0.0120 - acc: 0.9964
Epoch 9/10
  800/60000 [..............................] - ETA: 22s - loss: 0.0025 - acc: 0.9988

60000/60000 [==============================] - 22s 367us/step - loss: 0.0109 - acc: 0.9968
Epoch 10/10
54944/60000 [==========================>...] - ETA: 1s - loss: 0.0103 - acc: 0.9973

60000/60000 [==============================] - 22s 371us/step - loss: 0.0107 - acc: 0.9972
Training (Keras) Elaspsed Time: 223.4511468410492


Theano trains in roughly the same time frame as TensorFlow under Keras.

In [55]:
# 8. Evaluate model on test data
start=time.time()

score = model.evaluate(X_test, Y_test, verbose=0)

print("Testing (Keras) Elaspsed Time: {}".format(time.time()-start))

print("Loss={}, Accuracy={}".format(score[0], score[1]))

Testing (Keras) Elaspsed Time: 0.9958136081695557
Loss=0.040779472253139465, Accuracy=0.9914


Accuracy for the Theano model is approximately the same as for the TensorFlow model.

But the coolest takeaway - *I can use the same Keras code for TensorFlow and for Theano*.  When I wrote the code that executed Theano, I had not used Theano at all!

In coming presentations, I will be looking at more models using Keras.  But I suspect that there will be constructs in TensorFlow and Theano not available in Keras.  To me, it appears that learning Keras first is likely best - that is how some courses on Udemy approach it.  However, knowing the backends like TensorFlow or Theano well enough to implement those special cases not handled by Keras will likely be necessary.